<a href="https://colab.research.google.com/github/componavt/wd_book/blob/master/programming_tasks/natural_disasters/vuleq_connect/vuleq_connect2024.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>


# This program draws earthquakes, volcanoes and the nearest connections between them at a certain distance on a map of the Earth according to the CSV files earthquakes_2023.csv and volcanoes_2023.csv

Эта программа отрисовывает на карте Земли землетрясения, вулканы и соединяет ближайшие пары на определенном расстоянии по данным из CSV-файлов earthquakes_2023.csv и volcanoes_2023.csv


For the program to work, you need two CSV files generated using SPARQL queries: https://w.wiki/AXz7 and https://w.wiki/AY2R

Для работы программы необходимо два CSV-файла, сгенерированные при помощи SPARQL-запросов: https://w.wiki/AXz7 и https://w.wiki/AY2R

In [1]:
import folium
import csv
import numpy as np
from geopy.distance import geodesic
from scipy.spatial import KDTree
import pprint # Pretty Print for objects

!wget https://raw.githubusercontent.com/componavt/wd_book/master/programming_tasks/natural_disasters/vuleq_connect/volcanoes_2024.csv
!wget https://raw.githubusercontent.com/componavt/wd_book/master/programming_tasks/natural_disasters/vuleq_connect/earthquakes_2024.csv

--2024-07-04 16:03:14--  https://raw.githubusercontent.com/componavt/wd_book/master/programming_tasks/natural_disasters/vuleq_connect/volcanoes_2024.csv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 149378 (146K) [text/plain]
Saving to: ‘volcanoes_2024.csv’

volcanoes_2024.csv  100%[===================>] 145.88K  --.-KB/s    in 0.02s   

2024-07-04 16:03:14 (5.86 MB/s) - ‘volcanoes_2024.csv’ saved [149378/149378]

--2024-07-04 16:03:14--  https://raw.githubusercontent.com/componavt/wd_book/master/programming_tasks/natural_disasters/vuleq_connect/earthquakes_2024.csv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.111.133, 185.199.110.133, 185.199.109.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185

In [6]:
!head -n 3 volcanoes_2024.csv
print('\n')
!head -n 3 earthquakes_2024.csv

volcano,volcanoLabel,location
http://www.wikidata.org/entity/Q255010,Parinacota,Point(-69.141611111 -18.165752777)
http://www.wikidata.org/entity/Q298119,Öræfajökull,Point(-16.642063888 64.025436111)


earthquake,earthquakeLabel,location
http://www.wikidata.org/entity/Q3984652,Q3984652,Point(16.009 39.881)
http://www.wikidata.org/entity/Q3984715,1481 Rhodes earthquake,Point(28.0 36.0)


In [9]:

m = folium.Map()
Buff_list1 = []
Buff_list2 = []
line_between_objects1 = []
line_between_objects2 = []
repeat_check1 = 0
repeat_check2 = 0
repeat_check11 = 0
repeat_check22 = 0

# Opening a CSV-file and processing it
with open("volcanoes_2024.csv", encoding='utf-8', newline='') as csvfile:
    reader1 = csv.DictReader(csvfile, delimiter=",")
    #zz = 0
    for row in reader1:
        #zz+=1
        #if(zz>10):
        #  break
        # Puy Pariou;Point(2.971484 45.796824) -> popup;point(Buff_list1)
		    # Editing the original coordinates

        pprint.pprint(row) # Prints the nicely formatted dictionary

        popup = row['volcanoLabel']
        cords = row['location'].replace("Point(", "").replace(")", "")
        # Lat = cords.split()
        (x,y) = cords.split()
        Buff_list1.extend([float(x), float(y)]) # Adding coordinates to buffer

        pprint.pprint(Buff_list1)

        # Coordinate processing
        cor = tuple(Buff_list1)
        Buff_list1.clear()
        if (repeat_check1 == cor[0] and repeat_check2 == cor[1]):
            continue
        line_between_objects1.append((cor[1], cor[0]))
        folium.Circle(radius=500, location=[cor[1], cor[0]], popup=popup, tooltip='Volcano ' + popup, color="red").add_to(m)
        repeat_check1 = cor[0]
        repeat_check2 = cor[1]
# The same function is only for earthquakes CVS-file
with open("earthquakes_2024.csv", encoding='utf-8', newline='') as csvfile:
    reader2 = csv.DictReader(csvfile, delimiter=",")
    #yy=0
    for row in reader2:
        #yy += 1
        #if(yy>10):
        #  break
        #print(yy, ": ")
        #pprint.pprint(row) # Prints the nicely formatted dictionary
        popup = row['earthquakeLabel']
        cords = row['location'].replace("Point(", "").replace(")", "")
        Lat = cords.split()
        Buff_list2.extend([float(Lat[0]), float(Lat[1])])
        cor = tuple(Buff_list2)
        Buff_list2.clear()
        if (repeat_check11 == cor[0] and repeat_check22 == cor[1]):
            continue
        line_between_objects2.append((cor[1], cor[0]))
        folium.Circle(radius=500, location=[cor[1], cor[0]], popup=popup, tooltip='Earthquake ' + popup,
                      color="black").add_to(m)
        repeat_check11 = cor[0]
        repeat_check22 = cor[1]

# Drawing a line between two coordinates using K-Demension Trees
	# The used algorithm is described in "Maneewongvatana and Mount" 1999.
	# The general idea is that the  is a binary tree, each of whose nodes represents an axis-aligned hyperrectangle.
	# Each node specifies an axis and splits the set of points based on whether their coordinate along that axis is greater than or less than a particular value.
tree1 = KDTree(line_between_objects1) # Creating KDTree with the values of our coordinates
dist = 63 # Minimal distance for creating a line (63 the maximum distance at which an earthquake affects a volcano)
closest_points = tree1.query(line_between_objects2, k=1, distance_upper_bound=dist)[1]

closest_pairs_check_array = []
for i in range(len(line_between_objects1)):
    if closest_points[i] != len(line_between_objects1):
        eq_location = line_between_objects2[i]
        volcano_location = line_between_objects1[closest_points[i]]
        distance = geodesic(eq_location, volcano_location).kilometers
        if distance <= dist:
            closest_pairs_check_array.append((eq_location, volcano_location, distance))
#Drawing lines
for pair in closest_pairs_check_array:
    folium.PolyLine([pair[0], pair[1]], color="purple", weight=1, opacity=1).add_to(m)
# Saving the map
m

Streaming output truncated to the last 5000 lines.
{'location': 'Point(140.433333 42.116667)',
 'volcano': 'http://www.wikidata.org/entity/Q11566097',
 'volcanoLabel': 'Nigorikawa'}
[140.433333, 42.116667]
{'location': 'Point(-28.1219 38.6675)',
 'volcano': 'http://www.wikidata.org/entity/Q8524971',
 'volcanoLabel': 'Urzelina (volcano)'}
[-28.1219, 38.6675]
{'location': 'Point(139.037222222 35.005)',
 'volcano': 'http://www.wikidata.org/entity/Q11479422',
 'volcanoLabel': 'Mount Sukumo'}
[139.037222222, 35.005]
{'location': 'Point(138.133333333 36.733333333)',
 'volcano': 'http://www.wikidata.org/entity/Q11666652',
 'volcanoLabel': 'Mount Iizuna'}
[138.133333333, 36.733333333]
{'location': 'Point(-156.84 21.11)',
 'volcano': 'http://www.wikidata.org/entity/Q7960063',
 'volcanoLabel': 'East Molokai Volcano'}
[-156.84, 21.11]
{'location': 'Point(130.33944444 32.76833333)',
 'volcano': 'http://www.wikidata.org/entity/Q11582573',
 'volcanoLabel': 'Mount Mayu'}
[130.33944444, 32.76833333]
{